<a href="https://colab.research.google.com/github/Xin-overclocked/2Plus_UMH/blob/main/Noise_Cancellation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Final product INTERFACE --> A noisy audio and output text input with clean audio output

- Want to train myself the model or use existing pretrained models?
- How to construct weights
- How to do ensemble method to enhance accuracy (if necessary)

In [10]:
# Logging to Hugging Face
from huggingface_hub import login

login()

# Install Libraries

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
# Install Libraries

# For noise cancellation with ConvTasNet
!pip install asteroid

# For free speech-to-text
!pip install vosk

#For audio processing
!pip install torchaudio

# For audio speech-to-text processing
!pip install git+https://github.com/openai/whisper.git

# Chatgpt API for text processing
!pip install openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.5/53.5 kB 905.7 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.6/59.6 kB 4.2 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 156.4/156.4 kB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.0/823.0 kB 20.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.5/72.5 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.2/519.2 kB 32.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.8/102.8 kB 6.6 MB/s eta 0:00:00
  Created wheel for julius: filename=julius-0.2.7-py3-none-any.whl size=21967 sha256=66f1a70b491567034b005d84decc623db7aaa409d

In [4]:
!wget https://alphacephei.com/vosk/models/vosk-model-en-us-0.22.zip

--2025-04-12 04:58:04--  https://alphacephei.com/vosk/models/vosk-model-en-us-0.22.zip
Resolving alphacephei.com (alphacephei.com)... 188.40.21.16, 2a01:4f8:13a:279f::2
Connecting to alphacephei.com (alphacephei.com)|188.40.21.16|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1913365522 (1.8G) [application/zip]
Saving to: ‘vosk-model-en-us-0.22.zip’

vosk-model-en-us-0. 100%[===================>]   1.78G  25.1MB/s    in 73s     

2025-04-12 04:59:18 (24.9 MB/s) - ‘vosk-model-en-us-0.22.zip’ saved [1913365522/1913365522]



In [5]:
!unzip vosk-model-en-us-0.22.zip

Archive:  vosk-model-en-us-0.22.zip
   creating: vosk-model-en-us-0.22/
   creating: vosk-model-en-us-0.22/am/
  inflating: vosk-model-en-us-0.22/am/final.mdl  
  inflating: vosk-model-en-us-0.22/am/tree  
   creating: vosk-model-en-us-0.22/ivector/
  inflating: vosk-model-en-us-0.22/ivector/final.dubm  
  inflating: vosk-model-en-us-0.22/ivector/final.ie  
  inflating: vosk-model-en-us-0.22/ivector/final.mat  
  inflating: vosk-model-en-us-0.22/ivector/splice.conf  
  inflating: vosk-model-en-us-0.22/ivector/global_cmvn.stats  
  inflating: vosk-model-en-us-0.22/ivector/online_cmvn.conf  
  inflating: vosk-model-en-us-0.22/README  
   creating: vosk-model-en-us-0.22/conf/
  inflating: vosk-model-en-us-0.22/conf/mfcc.conf  
  inflating: vosk-model-en-us-0.22/conf/model.conf  
   creating: vosk-model-en-us-0.22/graph/
  inflating: vosk-model-en-us-0.22/graph/disambig_tid.int  
   creating: vosk-model-en-us-0.22/graph/phones/
 extracting: vosk-model-en-us-0.22/graph/phones/optional_silen

In [26]:
!pip install pysoundfile

@article{reddy2019scalable,
  title={A Scalable Noisy Speech Dataset and Online Subjective Test Framework},
  author={Reddy, Chandan KA and Beyrami, Ebrahim and Pool, Jamie and Cutler, Ross and Srinivasan, Sriram and Gehrke, Johannes},
  journal={Proc. Interspeech 2019},
  pages={1816--1820},
  year={2019}
}

In [12]:
# Clone the MS-SNSD dataset repository

!git clone https://github.com/microsoft/MS-SNSD.git

fatal: destination path 'MS-SNSD' already exists and is not an empty directory.


In [27]:
import numpy as np
import pandas as pd
import IPython.display as ipd
import torch
import torchaudio
import asteroid.models as ast
import soundfile as sf
from scipy.io.wavfile import write

# Models

## DCCRN

We're not training now, just evaluating or inferring, so use the full network and fixed batch statistics.


---


During training, layers like Dropout and BatchNorm behave differently than during evaluation:

- Dropout randomly disables parts of the network to prevent overfitting.

- BatchNorm uses statistics from the batch rather than accumulated training stats.

In [44]:
# Check for GPU and set the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

if device.type == 'cuda':
    print(f"GPU Name: {torch.cuda.get_device_name(0)}")
else:
    print("GPU not available, using CPU. Processing might be slow.")
    print("Tip: Go to Runtime > Change runtime type and select GPU as Hardware accelerator for faster results.")

Using device: cpu
GPU not available, using CPU. Processing might be slow.
Tip: Go to Runtime > Change runtime type and select GPU as Hardware accelerator for faster results.


In [45]:
from asteroid.models import DCCRNet

In [46]:
# Load the pre-trained DCCRNet model
# This will download the model weights the first time you run it
model_id = "JorisCos/DCCRNet_Libri1Mix_enhsingle_16k"
print(f"Loading model: {model_id}...")
try:
    model_DCCRNet = DCCRNet.from_pretrained(model_id).to(device)
    model_DCCRNet.eval()
    print(f"Model {model_id} loaded successfully.")
    # Get the model's expected sample rate (usually 16kHz for this one)
    try:
        target_sr = model_DCCRNet.sample_rate
    except AttributeError:
        print("Model doesn't directly expose sample_rate, assuming 16000 Hz based on model ID.")
        target_sr = 16000
    print(f"Model expects sample rate: {target_sr} Hz")

except Exception as e:
    print(f"Error loading model {model_id}: {e}")
    print("Please check the model ID and your internet connection.")
    raise e

Loading model: JorisCos/DCCRNet_Libri1Mix_enhsingle_16k...


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Model JorisCos/DCCRNet_Libri1Mix_enhsingle_16k loaded successfully.
Model expects sample rate: 16000.0 Hz


# Preparing datasets

In [47]:
'''
1. Clean Speech
2. Noisy Speech
3. Metrics
4. for reference text clean speech

noisy speech -> models -> output "CLEANED" speech -> evaluate on metrics + reference text clean speech

'''

'\n1. Clean Speech\n2. Noisy Speech \n3. Metrics\n4. for reference text clean speech\n\nnoisy speech -> models -> output "CLEANED" speech -> evaluate on metrics + reference text clean speech\n\n'

In [48]:
# Load the clean_test audio file
cleantest0_waveform, sample_rate = torchaudio.load("/content/MS-SNSD/clean_test/clnsp0.wav")

# Play the audio
ipd.Audio(cleantest0_waveform.numpy(), rate=sample_rate)


In [49]:
# Load the noise_test audio file
noisetest0_waveform, sample_rate_noisetest0_waveform = torchaudio.load("/content/MS-SNSD/noise_test/AirConditioner_1.wav")

# Play the audio
print(sample_rate_noisetest0_waveform)
ipd.Audio(noisetest0_waveform.numpy(), rate=sample_rate)

16000


In [50]:
# Load the noise_test audio file
noisetrain0_waveform, sample_rate_train0 = torchaudio.load("/content/MS-SNSD/noise_train/AirConditioner_1.wav")

# Play the audio
ipd.Audio(noisetrain0_waveform.numpy(), rate=sample_rate_train0)

### AirConditioner_Noise Mix

In [51]:
# Functions from MS-SNSD github
import sys
sys.path.append('/content/MS-SNSD')
from audiolib import snr_mixer

In [52]:
cleantest0_waveform = np.squeeze(cleantest0_waveform)
noisetest0_waveform = np.squeeze(noisetest0_waveform)

# Match lengths
if len(noisetest0_waveform) < len(cleantest0_waveform):
    repeat_factor = int(np.ceil(len(cleantest0_waveform) / len(noisetest0_waveform)))
    noisetest0_waveform = np.tile(noisetest0_waveform, repeat_factor)[:len(cleantest0_waveform)]
else:
    noisetest0_waveform = noisetest0_waveform[:len(cleantest0_waveform)]

# 10 dB SNR
clean0_out, noise0_out, noisy0 = snr_mixer(cleantest0_waveform, noisetest0_waveform, snr=10)

# Play audio
print("Noisy Audio Clip")
ipd.display(ipd.Audio(noisy0, rate=sample_rate))
print("Clean Audio Clip")
ipd.display(ipd.Audio(clean0_out, rate=sample_rate))


Noisy Audio Clip


Clean Audio Clip


In [53]:
print(type(noisy0))

<class 'torch.Tensor'>


In [54]:
noisy0 = noisy0.squeeze().cpu().numpy().astype('float32')

In [55]:
write("/content/drive/MyDrive/noisy_audio_clips/noisy0.wav", sample_rate, noisy0)

### Speech-To-Text Function (Whisper)

In [56]:
import whisper

model_Whisper = whisper.load_model("turbo")

In [57]:
# load audio and pad/trim it to fit 30 seconds
audio = whisper.load_audio("/content/MS-SNSD/clean_test/clnsp0.wav")
audio = whisper.pad_or_trim(audio)

In [40]:
# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio, n_mels=model_Whisper.dims.n_mels).to(model_Whisper.device)

In [41]:
# detect the spoken language
_, probs = model_Whisper.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

Detected language: en


##### Run for 5mins - 6mins (11 secs audio clip) - For CPU
Run for 2.5mins (11 secs audio clip) - For v2-8 TPU

In [43]:
# decode the audio
options = whisper.DecodingOptions()
result = whisper.decode(model_Whisper, mel, options)

In [45]:
# Set your Google Drive path
save_path = "/content/drive/MyDrive/data_noise/cleantext0_transcription.txt"

# Write the transcription to the file
with open(save_path, "w", encoding="utf-8") as f:
    f.write(f"Detected language:{max(probs, key=probs.get)}\n")
    f.write(result.text)

In [46]:
# print the recognized text
print(result.text)

She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


In [47]:
clean0_text = result.text

In [48]:
print(clean0_text)

She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


### Speech-To-Text Function (Vosk)

In [30]:
from vosk import Model, KaldiRecognizer
import os
import wave
import json

In [31]:
model_Vosk = Model('vosk-model-en-us-0.22')

# Run Models to Clean Noise

In [51]:
def preprocessing_noisy_audio_clip_DCCRNet(noisy0):
  print(f"\nUsing existing 'noisy0' variable.")

  # Assume noisy0 is your variable (currently a NumPy array)
  # Make sure you have the sample rate it was created with
  original_sr = 16000

  # --- Check if noisy0 is NumPy and Convert to PyTorch Tensor ---
  if isinstance(noisy0, np.ndarray):
      print("Converting NumPy array 'noisy0' to PyTorch tensor...")
      # Convert numpy array to PyTorch tensor. Use .float() as models usually expect float32
      noisy_tensor = torch.from_numpy(noisy0).float()
  elif torch.is_tensor(noisy0):
      print("'noisy0' is already a PyTorch tensor.")
      noisy_tensor = noisy0 # Use it directly if it's already a tensor
  else:
      # Handle other potential types or raise an error
      raise TypeError(f"Variable 'noisy0' is not a NumPy array or PyTorch tensor, but type: {type(noisy0)}")

  # --- Move tensor to device ---
  # Now use the *tensor* version ('noisy_tensor')
  noisy_waveform = noisy_tensor.to(device)
  print(f"Tensor moved to device: {noisy_waveform.device}")
  print(f"Original SR: {original_sr} Hz, Tensor Shape: {noisy_waveform.shape}")

  # --- Display Original Audio ---
  # ipd.Audio works best with NumPy arrays or lists on CPU
  print("\nOriginal Noisy Audio:")
  try:
      # Use the original numpy array if available and valid
      if isinstance(noisy0, np.ndarray):
          display_data = noisy0
      else: # Otherwise convert the tensor back to numpy on CPU
          display_data = noisy_waveform.cpu().numpy()
      ipd.display(ipd.Audio(data=display_data, rate=original_sr))
  except Exception as e:
      print(f"Could not play audio: {e}")


  # --- Preprocessing (Continues using the PyTorch tensor 'noisy_waveform') ---
  print("Starting preprocessing...")
  # 1. Resample if necessary
  if original_sr != target_sr:
      print(f"Resampling from {original_sr} Hz to {target_sr} Hz...")
      resampler = torchaudio.transforms.Resample(orig_freq=original_sr, new_freq=target_sr).to(device)
      noisy_waveform = resampler(noisy_waveform)
      print(f"Resampled shape: {noisy_waveform.shape}")

  # 2. Convert to Mono if necessary (DCCRNet expects mono)
  if noisy_waveform.dim() > 1 and noisy_waveform.shape[0] > 1: # Check if tensor has channel dim and > 1 channel
      print(f"Converting to mono...")
      noisy_waveform = torch.mean(noisy_waveform, dim=0, keepdim=True) # Average channels
      print(f"Mono shape: {noisy_waveform.shape}")

  # 3. Ensure correct shape for the model (batch, time)
  if noisy_waveform.dim() == 2 and noisy_waveform.shape[0] == 1: # If shape (1, time)
    noisy_waveform = noisy_waveform.squeeze(0) # Shape: (time)
  elif noisy_waveform.dim() > 1: # Handle unexpected extra dims if necessary
      print("Warning: Tensor has more dimensions than expected after mono conversion. Taking first element.")
      noisy_waveform = noisy_waveform[0] # Or adapt as needed

  # Add batch dimension -> (1, time)
  noisy_waveform = noisy_waveform.unsqueeze(0)
  print(f"Final input shape for model: {noisy_waveform.shape}")
  return noisy_waveform

In [52]:
# Noise Cancellation with DCCRNet

In [93]:
def DCCRNet_noise_cancellation(noisy_waveform0: torch.Tensor) -> torch.Tensor:
    print("\nPerforming noise cancellation on DCCRNet Model...")
    with torch.no_grad():  # Disable gradient calculations for inference
        estimated_clean_waveform = model_DCCRNet(noisy_waveform0)
    print(f"Inference complete. Output shape: {estimated_clean_waveform.shape}")
    return estimated_clean_waveform

In [81]:
def play_cleaned_noisy_audio_toNumpy(estimated_clean_waveform):
    print(type(estimated_clean_waveform))
    print(estimated_clean_waveform.shape)

    # Ensure tensor is on CPU before converting
    audio_np_cleannoisy0 = estimated_clean_waveform.squeeze().detach().cpu().numpy()

    sample_rate = 16000
    print("Cleaned Noisy Audio Clip: noisy0")
    ipd.display(ipd.Audio(audio_np_cleannoisy0, rate=sample_rate))

    return audio_np_cleannoisy0

In [94]:
noisy_waveform0 = preprocessing_noisy_audio_clip_DCCRNet(noisy0)


Using existing 'noisy0' variable.
Converting NumPy array 'noisy0' to PyTorch tensor...
Tensor moved to device: cpu
Original SR: 16000 Hz, Tensor Shape: torch.Size([176320])

Original Noisy Audio:


Starting preprocessing...
Final input shape for model: torch.Size([1, 176320])


In [95]:
print(type(noisy_waveform0))

<class 'torch.Tensor'>


In [98]:
clean_noisy0_tensors = DCCRNet_noise_cancellation(noisy_waveform0)


Performing noise cancellation on DCCRNet Model...
Inference complete. Output shape: torch.Size([1, 1, 176320])


In [99]:
print(type(clean_noisy0_tensors))

<class 'torch.Tensor'>


In [100]:
clean_noisy0_numpy = play_cleaned_noisy_audio_toNumpy(clean_noisy0_tensors)

<class 'torch.Tensor'>
torch.Size([1, 1, 176320])
Cleaned Noisy Audio Clip: noisy0


# Evaluation on Metrics

### Evaluating the effectiveness of noise cancellation (NC)

In [83]:
from pystoi import stoi
from scipy.io import wavfile
from pesq import pesq

In [84]:
sample_rate = 16000

In [120]:
# def calculate_mse(clean_signal, processed_signal):
#     return np.mean((clean_signal - processed_signal) ** 2)

def calculate_mse_torch(clean_signal: torch.Tensor, processed_signal: torch.Tensor) -> torch.Tensor:
    return torch.mean((clean_signal - processed_signal) ** 2)

In [112]:
# def calculate_pesq(clean_signal, processed_signal, sample_rate):
#     return pesq(sample_rate, clean_signal, processed_signal, 'wb')
#     # 'wb' = wideband

def calculate_pesq(clean_signal: torch.Tensor, processed_signal: torch.Tensor, sample_rate: int) -> float:
    clean_np = clean_signal.squeeze().detach().cpu().numpy()
    processed_np = processed_signal.squeeze().detach().cpu().numpy()
    return pesq(sample_rate, clean_np, processed_np, 'wb')  # 'wb' = wideband

In [113]:
# def calculate_stoi(clean_signal, processed_signal, sample_rate):
#     return stoi(clean_signal, processed_signal, sample_rate, extended=False)

def calculate_stoi(clean_signal: torch.Tensor, processed_signal: torch.Tensor, sample_rate: int) -> float:
    clean_np = clean_signal.squeeze().detach().cpu().numpy()
    processed_np = processed_signal.squeeze().detach().cpu().numpy()
    return stoi(clean_np, processed_np, sample_rate, extended=False)

In [114]:
# def calculate_insertion_loss(noise_only_signal, noise_with_anc_signal):
#     noise_power = np.mean(noise_only_signal ** 2)
#     anc_power = np.mean(noise_with_anc_signal ** 2)
#     insertion_loss = 10 * np.log10(noise_power / anc_power)
#     return insertion_loss

def calculate_insertion_loss(noise_only_signal: torch.Tensor, noise_with_anc_signal: torch.Tensor) -> float:
    noise_np = noise_only_signal.squeeze().detach().cpu().numpy()
    anc_np = noise_with_anc_signal.squeeze().detach().cpu().numpy()
    noise_power = np.mean(noise_np ** 2)
    anc_power = np.mean(anc_np ** 2)
    insertion_loss = 10 * np.log10(noise_power / anc_power)
    return insertion_loss

In [107]:
print(type(clean0_out))

<class 'torch.Tensor'>


In [106]:
print(type(clean_noisy0_tensors))

<class 'torch.Tensor'>


In [111]:
calculate_mse_torch(clean0_out,clean_noisy0_tensors)

tensor(0.0022)

An MSE of 0.0022 suggests high similarity between "noisy0", clean and processed signal, which usually means effective noise suppression with minimal distortion

In [115]:
calculate_pesq(clean0_out,clean_noisy0_tensors, sample_rate)

2.010915756225586

This falls into the "Poor" category.

It suggests there’s still noticeable distortion or degradation in perceived audio quality, even though the intelligibility (STOI) is excellent.

In [116]:
calculate_stoi(clean0_out,clean_noisy0_tensors, sample_rate)

np.float64(0.9702082388273956)

Suggests excellent speech clarity after noise cancellation.

Nearly indistinguishable from clean speech in terms of understandability.

In [118]:
calculate_insertion_loss(clean0_out, clean_noisy0_tensors)

np.float32(15.085939)

An insertion loss of 15.08 dB indicates that your noise cancellation algorithm is highly effective at suppressing background noise.



---

DCCRNet is great at removing noise and preserving clarity, it may still introduce artifacts (e.g., muffling, robotic sounds), which hurts perceived naturalness.
- Can improve in terms of natural sound quality (as perceived by listeners)

### Evaluating Speech-To-Text Effectiveness

In [122]:
# Speech to text
# Evaluate on Word Error Rate metric (WER)

In [4]:
!pip install jiwer

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 35.0 MB/s eta 0:00:00


In [13]:
# load audio and pad/trim it to fit 30 seconds
audio_test0 = whisper.load_audio("/content/MS-SNSD/clean_test/clnsp0.wav")
audio = whisper.pad_or_trim(audio_test0)

# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio, n_mels=model_Whisper.dims.n_mels).to(model_Whisper.device)

# detect the spoken language
_, probs = model_Whisper.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# decode the audio
options = whisper.DecodingOptions()
refer_result = whisper.decode(model_Whisper, mel, options)

# Set your Google Drive path
save_path = "/content/drive/MyDrive/data_noise/cleantext0_transcription.txt"

# Write the transcription to the file
with open(save_path, "w", encoding="utf-8") as f:
    f.write(f"Detected language:{max(probs, key=probs.get)}\n")
    f.write(refer_result.text)

# print the recognized text
print(refer_result.text)

Detected language: en
She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


In [5]:
from jiwer import wer

In [12]:
# load audio and pad/trim it to fit 30 seconds
audio_test0 = whisper.load_audio("/content/drive/MyDrive/noisy_audio_clips/noisy0.wav")
audio = whisper.pad_or_trim(audio_test0)

# make log-Mel spectrogram and move to the same device as the model
mel = whisper.log_mel_spectrogram(audio, n_mels=model_Whisper.dims.n_mels).to(model_Whisper.device)

# detect the spoken language
_, probs = model_Whisper.detect_language(mel)
print(f"Detected language: {max(probs, key=probs.get)}")

# decode the audio
options = whisper.DecodingOptions()
result = whisper.decode(model_Whisper, mel, options)

# Set your Google Drive path
save_path = "/content/drive/MyDrive/data_noise/cleantext0_transcription.txt"

# Write the transcription to the file
with open(save_path, "w", encoding="utf-8") as f:
    f.write(f"Detected language:{max(probs, key=probs.get)}\n")
    f.write(result.text)

# print the recognized text
print(result.text)

Detected language: en
She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


In [15]:
noisy_text = result.text
reference_text = refer_result.text

In [17]:
print(noisy_text)

She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


In [18]:
print(reference_text)

She seemed irritated. You've got no business up here. You took me by surprise. There would still be plenty of moments of regret and sadness and guilty relief. A warm breeze played across it, moving it like waves.


In [20]:
# test_a = "this is a test"
# test_b = "this is test"

reference = reference_text
hypothesis = noisy_text

score = wer(reference, hypothesis)
print(f"WER: {score:.3f}")

WER: 0.000


In [23]:
# model_Vosk
print(type(audio_test0))

<class 'numpy.ndarray'>


In [24]:
import io
from vosk import Model, KaldiRecognizer
import json

In [32]:
def transcribe_numpy_audio(audio_array: np.ndarray, model_Vosk, sample_rate: int = 16000) -> str:
    # Ensure audio is in float32 [-1, 1]
    if audio_array.dtype != np.float32:
        audio_array = audio_array.astype(np.float32)

    # Convert to bytes in 16-bit PCM WAV format using an in-memory buffer
    buffer = io.BytesIO()
    sf.write(buffer, audio_array, sample_rate, format='WAV', subtype='PCM_16')
    buffer.seek(0)

    # Use Vosk recognizer on the buffer
    rec = KaldiRecognizer(model_Vosk, sample_rate)

    results = []
    while True:
        data = buffer.read(4000)
        if len(data) == 0:
            break
        if rec.AcceptWaveform(data):
            result = json.loads(rec.Result())
            results.append(result.get("text", ""))

    final_result = json.loads(rec.FinalResult())
    results.append(final_result.get("text", ""))

    transcription = " ".join(results)
    return transcription


In [62]:
text_hypothesis = transcribe_numpy_audio(audio_test0, model_Vosk, sample_rate=16000)
print("Transcribed Text:", text_hypothesis)

Transcribed Text: she seemed irritated you've got no business up here you took me by surprise there would still be plenty of moments of regret and sadness and guilty relief a warm breeze played across it moving it like waves


In [58]:
print(type(clean0_out))

<class 'torch.Tensor'>


In [59]:
import torch
import numpy as np

def tensor_to_numpy(tensor: torch.Tensor) -> np.ndarray:
    """
    Converts a PyTorch tensor to a NumPy array.

    Args:
        tensor (torch.Tensor): The input tensor.

    Returns:
        np.ndarray: The converted NumPy array.
    """
    if tensor.requires_grad:
        tensor = tensor.detach()
    return tensor.cpu().numpy()


In [60]:
clean0_numpy = tensor_to_numpy(clean0_out)

In [63]:
text_reference = transcribe_numpy_audio(clean0_numpy, model_Vosk, sample_rate=16000)
print("Transcribed Text:", text_reference)

Transcribed Text: she seemed irritated you've got no business up here you took me by surprise there would still be plenty of moments of regret and sadness and guilty relief a warm breeze played across it moving it like waves


In [64]:
reference = text_reference
hypothesis = text_hypothesis

score = wer(reference, hypothesis)
print(f"WER: {score:.3f}")

WER: 0.000
